In [ ]:
#Model Commit

In [3]:
!pip install huggingface_hub python-dotenv

In [4]:
from dotenv import load_dotenv
import os
from huggingface_hub import login, hf_hub_download

# Load environment variables from .env file
load_dotenv()

# Retrieve the Hugging Face token from the environment variable
hf_token = os.getenv("HF_TOKEN")

# Ensure the token is present
if not hf_token:
    raise ValueError("Hugging Face token not found. Make sure your .env file is configured correctly and HF_TOKEN is set.")

# Authenticate with Hugging Face using the token
login(token=hf_token)

Token has not been saved to git credential helper. Pass `add_to_git_credential=True` if you want to set the git credential as well.
Token is valid (permission: write).
Your token has been saved to /root/.cache/huggingface/token
Login successful


In [7]:
import sys

# Install git
!conda install -c anaconda git -y

# Install git-lfs
!conda install -c conda-forge git-lfs -y

# Set up git-lfs (you only need to do this once)
!git lfs install

print("Installation completed.")

Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 23.9.0
  latest version: 24.1.2

Please update conda by running

    $ conda update -n base -c defaults conda

Or to minimize the number of packages updated during conda update use

     conda install conda=24.1.2



## Package Plan ##

  environment location: /opt/conda

  added / updated specs:
    - git


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    ca-certificates-2023.08.22 |       h06a4308_0         130 KB  anaconda
    certifi-2023.11.17         |  py310h06a4308_0         159 KB  anaconda
    curl-8.4.0                 |       hdbd6064_0          90 KB  anaconda
    gdbm-1.18                  |       hd4cb3f1_4         193 KB  anaconda
    gettext-0.21.0             |       h39681ba_1         3.4 MB  anaconda
    git-2.40.1                 | pl5340h36fbf9e_1         9.9 MB
    libcu

In [8]:
from huggingface_hub import HfApi, HfFolder, Repository
import os

# Define the path to your model and the name of the Hugging Face repository
local_model_directory = "./workspace/outputs/NousResearch/Nous-Hermes-2-Mistral-7B-DPO/a83a8c0d-5838-47ac-ba15-69da87e94619/epoch_3/step_final/"
repo_name = "clau_creat"
username = "arthrod"  # Replace with your Hugging Face username
repo_id = f"{username}/{repo_name}"

# Authenticate with Hugging Face
#token = HfFolder.get_token()
#if token is None:
#    raise ValueError("You must be logged in to Hugging Face. Use `huggingface-cli login`.")

# Initialize the HfApi object
api = HfApi()

# Check if the repository exists, if not, create it
try:
    api.repo_info(repo_id=repo_id)
except Exception as e:
    print(f"Repository {repo_id} does not exist. Creating it...")
    api.create_repo(token=token, name=repo_name, organization=username, private=False)  # Set private=True for a private repository

# Clone the repository (if necessary) and copy your model files into it
repo_url = f"https://huggingface.co/{repo_id}"
repo_local_path = os.path.join(os.getcwd(), repo_name)

# If the repo directory doesn't exist, clone it. Otherwise, just pull the latest changes
if not os.path.isdir(repo_local_path):
    repo = Repository(local_dir=repo_local_path, clone_from=repo_url, use_auth_token=True)
else:
    repo = Repository(local_dir=repo_local_path, use_auth_token=True)
    repo.git_pull()

# Copy files from your model directory to the cloned repository
for file_name in os.listdir(local_model_directory):
    src_file_path = os.path.join(local_model_directory, file_name)
    dst_file_path = os.path.join(repo_local_path, file_name)
    if os.path.isfile(src_file_path):
        os.replace(src_file_path, dst_file_path)

# Commit and push the changes to the repository
repo.git_add(auto_lfs_track=True)
repo.git_commit("Upload model to Hugging Face Hub")
repo.git_push()

print(f"Model successfully uploaded to: https://huggingface.co/{repo_id}")

/opt/conda/lib/python3.10/site-packages/huggingface_hub/utils/_deprecation.py:131: FutureWarning: 'Repository' (from 'huggingface_hub.repository') is deprecated and will be removed from version '1.0'. Please prefer the http-based alternatives instead. Given its large adoption in legacy code, the complete removal is only planned on next major release.
For more details, please read https://huggingface.co/docs/huggingface_hub/concepts/git_vs_http.
  warnings.warn(warning_message, FutureWarning)


ValueError: If not specifying `clone_from`, you need to pass Repository a valid git clone.

In [14]:
!pip install pickleshare

In [16]:
%cd /outputs/NousResearch/Nous-Hermes-2-Mistral-7B-DPO/a83a8c0d-5838-47ac-ba15-69da87e94619/epoch_3/step_final

[Errno 2] No such file or directory: '/outputs/NousResearch/Nous-Hermes-2-Mistral-7B-DPO/a83a8c0d-5838-47ac-ba15-69da87e94619/epoch_3/step_final'
/workspace/outputs/NousResearch/Nous-Hermes-2-Mistral-7B-DPO/a83a8c0d-5838-47ac-ba15-69da87e94619/epoch_3


In [17]:
!pwd

/workspace/outputs/NousResearch/Nous-Hermes-2-Mistral-7B-DPO/a83a8c0d-5838-47ac-ba15-69da87e94619/epoch_3


In [ ]:
from huggingface_hub import HfApi, HfFolder
import os

def upload_files_to_hub(directory, repo_name, username, private=False):
    """
    Uploads files from a specified directory to a Hugging Face Hub repository using the HTTP-based API.

    Parameters:
    - directory: The local directory where your files are stored.
    - repo_name: The name of the repository on the Hugging Face Hub.
    - username: Your Hugging Face username.
    - private: (Optional) Whether to create a private repository. Defaults to False.
    """
    # Ensure the directory is an absolute path
    directory = os.path.abspath(directory)

    # Instantiate HfApi object
    api = HfApi()

    # Get token
    token = HfFolder.get_token()
    if token is None:
        raise ValueError("You must be logged in to Hugging Face. Use `huggingface-cli login`.")

    # Correctly specify the repository ID
    repo_id = f"{username}/{repo_name}"

    # Check if the repository exists, and create it if it does not
    try:
        repo_url = api.create_repo(token=token, repo_id=repo_id, private=private, exist_ok=True)
    except Exception as e:
        print(f"Error creating repository: {e}")
        return

    # Upload directory to repository
    try:
        api.upload_folder(token=token, repo_id=repo_id, folder_path=directory, path_in_repo="")
        print(f"Files successfully uploaded to: {repo_url}")
    except Exception as e:
        print(f"Error uploading files to the repository: {e}")

# Example usage
upload_files_to_hub(directory=".", repo_name="clau_creat", username="arthrod", private=False)

Upload 3 LFS files:   0%|          | 0/3 [00:00<?, ?it/s]

tokenizer.model:   0%|          | 0.00/493k [00:00<?, ?B/s]

pytorch_model-00001-of-00002.bin:   0%|          | 0.00/9.94G [00:00<?, ?B/s]

pytorch_model-00002-of-00002.bin:   0%|          | 0.00/4.54G [00:00<?, ?B/s]